In [10]:
!pip install yfinance
!pip install pandas_datareader
import yfinance as yf
import pandas as pd
import datetime as dt
import numpy as np


# Override pandas_datareader with yfinance
yf.pdr_override()
rf = 0.048
initial_investment=100000


In [34]:
excel_file = 'stockprice.xlsx'  # Replace 'stockprice.xlsx' with your Excel file name
stock_df = pd.read_excel(excel_file)

# Drop rows with any NaN values
stock_df.dropna(how='any', inplace=True)

# Reset index after dropping rows
stock_df.reset_index(drop=True, inplace=True)

# Write DataFrame to CSV file
csv_file = 'stock_data.csv'  # Name for the CSV file to be created
stock_df.to_csv(csv_file, index=False) 
stock_df

Date            FPT    TCB           MBB
0    20/03/2024  114500.000000  42300  24150.000000
1    19/03/2024  112000.000000  40300  23200.000000
2    18/03/2024  113000.000000  40100  23200.000000
3    15/03/2024  116000.000000  41400  23800.000000
4    14/03/2024  117000.000000  41400  23450.000000
..          ...            ...    ...           ...
723  28/04/2021   48280.524295  39950  15837.319435
724  27/04/2021   48220.771171  39500  15497.013397
725  26/04/2021   48400.030543  39450  15497.013397
726  23/04/2021   49595.093026  40500  15863.496822
727  22/04/2021   47802.499302  39700  15287.594297

[728 rows x 4 columns]

In [35]:
daily_returns_df = stock_df.iloc[:, 1:].pct_change() * 100
daily_returns_df.replace(np.nan, 0, inplace = True)
daily_returns_df

FPT       TCB       MBB
0    0.000000  0.000000  0.000000
1   -2.183406 -4.728132 -3.933747
2    0.892857 -0.496278  0.000000
3    2.654867  3.241895  2.586207
4    0.862069  0.000000 -1.470588
..        ...       ...       ...
723 -0.123609 -2.560976 -0.329489
724 -0.123762 -1.126408 -2.148760
725  0.371747 -0.126582  0.000000
726  2.469136  2.661597  2.364865
727 -3.614458 -1.975309 -3.630363

[728 rows x 3 columns]

In [36]:
daily_returns_df.insert(0, "Date", stock_df['Date'])
daily_returns_df

Date       FPT       TCB       MBB
0    20/03/2024  0.000000  0.000000  0.000000
1    19/03/2024 -2.183406 -4.728132 -3.933747
2    18/03/2024  0.892857 -0.496278  0.000000
3    15/03/2024  2.654867  3.241895  2.586207
4    14/03/2024  0.862069  0.000000 -1.470588
..          ...       ...       ...       ...
723  28/04/2021 -0.123609 -2.560976 -0.329489
724  27/04/2021 -0.123762 -1.126408 -2.148760
725  26/04/2021  0.371747 -0.126582  0.000000
726  23/04/2021  2.469136  2.661597  2.364865
727  22/04/2021 -3.614458 -1.975309 -3.630363

[728 rows x 4 columns]

In [37]:
import random # random weight function
n = len(stock_df.columns)-1
def generate_portfolio_weights(n):
    weights = []
    for i in range(n):
        weights.append(random.random())
        
    # let's make the sum of all weights add up to 1
    weights = weights/np.sum(weights)
    return weights
weights=generate_portfolio_weights(n)
def price_scaling(raw_prices_df):
    scaled_prices_df = raw_prices_df.copy()
    for i in raw_prices_df.columns[1:]:
          scaled_prices_df[i] = raw_prices_df[i]/raw_prices_df[i].iloc[0]
    return scaled_prices_df

In [38]:
portfolio_df = stock_df.copy()
scaled_df = price_scaling(portfolio_df)
scaled_df
for i, stock in enumerate(scaled_df.columns[1:]):
    portfolio_df[stock] = weights[i] * scaled_df[stock]  * initial_investment
portfolio_df.round(1)

Date      FPT      TCB      MBB
0    20/03/2024  30524.4  11778.8  57696.7
1    19/03/2024  29858.0  11221.9  55427.1
2    18/03/2024  30124.6  11166.2  55427.1
3    15/03/2024  30924.3  11528.2  56860.5
4    14/03/2024  31190.9  11528.2  56024.3
..          ...      ...      ...      ...
723  28/04/2021  12871.1  11124.5  37836.9
724  27/04/2021  12855.1  10999.2  37023.9
725  26/04/2021  12902.9  10985.2  37023.9
726  23/04/2021  13221.5  11277.6  37899.4
727  22/04/2021  12743.6  11054.8  36523.6

[728 rows x 4 columns]

In [39]:
def asset_allocation(df, weights, initial_investment):
    portfolio_df = df.copy()

    # Scale stock prices using the "price_scaling" function that we defined earlier (Make them all start at 1)
    scaled_df = price_scaling(df)
  
    for i, stock in enumerate(scaled_df.columns[1:]):
        portfolio_df[stock] = scaled_df[stock] * weights[i] * initial_investment

    # Sum up all values and place the result in a new column titled "portfolio value [$]" 
    # Note that we excluded the date column from this calculation
    portfolio_df['Portfolio Value [$]'] = portfolio_df[portfolio_df != 'Date'].sum(axis = 1, numeric_only = True)
            
    # Calculate the portfolio percentage daily return and replace NaNs with zeros
    portfolio_df['Portfolio Daily Return [%]'] = portfolio_df['Portfolio Value [$]'].pct_change(1) * 100 
    portfolio_df.replace(np.nan, 0, inplace = True)
    
    return portfolio_df

In [40]:
def simulation_engine(weights, initial_investment):
    # Perform asset allocation using the random weights (sent as arguments to the function)
    portfolio_df = asset_allocation(stock_df, weights, initial_investment)
  
    # Calculate the return on the investment 
    # Return on investment is calculated using the last final value of the portfolio compared to its initial value
    return_on_investment = ((portfolio_df['Portfolio Value [$]'].iloc[-1:] - 
                             portfolio_df['Portfolio Value [$]'].iloc[0])/ 
                             portfolio_df['Portfolio Value [$]'].iloc[0]) * 100
  
    # Daily change of every stock in the portfolio (Note that we dropped the date, portfolio daily worth and daily % returns) 
    portfolio_daily_return_df = portfolio_df.drop(columns = ['Date', 'Portfolio Value [$]', 'Portfolio Daily Return [%]'])
    portfolio_daily_return_df = portfolio_daily_return_df.pct_change(1) 
  
    # Portfolio Expected Return formula
    expected_portfolio_return = np.sum(weights * portfolio_daily_return_df.mean() ) * 252
  
    covariance = portfolio_daily_return_df.cov() * 252 
    expected_volatility = np.sqrt(np.dot(weights.T, np.dot(covariance, weights)))

     
    # Calculate Sharpe ratio
    sharpe_ratio = (expected_portfolio_return - rf)/expected_volatility 
    return expected_portfolio_return, expected_volatility, sharpe_ratio, portfolio_df['Portfolio Value [$]'][-1:].values[0], return_on_investment.values[0]
  

In [41]:
sim_runs = 10000
# Placeholder to store all weights
weights_runs = np.zeros((sim_runs, n))

# Placeholder to store all Sharpe ratios
sharpe_ratio_runs = np.zeros(sim_runs)

# Placeholder to store all expected returns
expected_portfolio_returns_runs = np.zeros(sim_runs)

# Placeholder to store all volatility values
volatility_runs = np.zeros(sim_runs)

# Placeholder to store all returns on investment
return_on_investment_runs = np.zeros(sim_runs)

# Placeholder to store all final portfolio values
final_value_runs = np.zeros(sim_runs)

for i in range(sim_runs):
    # Generate random weights 
    weights = generate_portfolio_weights(n)
    # Store the weights
    weights_runs[i,:] = weights
    
    # Call "simulation_engine" function and store Sharpe ratio, return and volatility
    # Note that asset allocation is performed using the "asset_allocation" function  
    expected_portfolio_returns_runs[i], volatility_runs[i], sharpe_ratio_runs[i], final_value_runs[i], return_on_investment_runs[i] = simulation_engine(weights, initial_investment)
    print("Simulation Run = {}".format(i))   
    print("Weights = {}, Final Value = ${:.2f}, Sharpe Ratio = {:.2f}".format(weights_runs[i].round(3), final_value_runs[i], sharpe_ratio_runs[i]))   
    print('\n')

Simulation Run = 0
Weights = [0.115 0.487 0.398], Final Value = $75717.09, Sharpe Ratio = -0.33


Simulation Run = 1
Weights = [0.456 0.031 0.513], Final Value = $54410.53, Sharpe Ratio = -0.84


Simulation Run = 2
Weights = [0.367 0.363 0.27 ], Final Value = $66488.71, Sharpe Ratio = -0.59


Simulation Run = 3
Weights = [0.393 0.144 0.463], Final Value = $59231.69, Sharpe Ratio = -0.73


Simulation Run = 4
Weights = [0.42  0.386 0.194], Final Value = $66030.57, Sharpe Ratio = -0.62


Simulation Run = 5
Weights = [0.012 0.765 0.223], Final Value = $86436.61, Sharpe Ratio = -0.13


Simulation Run = 6
Weights = [0.491 0.493 0.017], Final Value = $67771.96, Sharpe Ratio = -0.60


Simulation Run = 7
Weights = [0.324 0.26  0.416], Final Value = $64282.40, Sharpe Ratio = -0.61


Simulation Run = 8
Weights = [0.316 0.36  0.324], Final Value = $67506.51, Sharpe Ratio = -0.55


Simulation Run = 9
Weights = [0.15  0.591 0.259], Final Value = $78119.38, Sharpe Ratio = -0.30


Simulation Run = 10


Simulation Run = 83
Weights = [0.514 0.33  0.156], Final Value = $62296.11, Sharpe Ratio = -0.72


Simulation Run = 84
Weights = [0.296 0.273 0.431], Final Value = $65254.29, Sharpe Ratio = -0.58


Simulation Run = 85
Weights = [0.192 0.68  0.129], Final Value = $79947.41, Sharpe Ratio = -0.28


Simulation Run = 86
Weights = [0.634 0.316 0.05 ], Final Value = $59308.16, Sharpe Ratio = -0.82


Simulation Run = 87
Weights = [0.178 0.553 0.269], Final Value = $76354.94, Sharpe Ratio = -0.34


Simulation Run = 88
Weights = [0.386 0.361 0.253], Final Value = $66000.11, Sharpe Ratio = -0.60


Simulation Run = 89
Weights = [0.451 0.024 0.525], Final Value = $54338.73, Sharpe Ratio = -0.84


Simulation Run = 90
Weights = [0.288 0.413 0.299], Final Value = $69715.72, Sharpe Ratio = -0.50


Simulation Run = 91
Weights = [0.377 0.268 0.356], Final Value = $63351.31, Sharpe Ratio = -0.65


Simulation Run = 92
Weights = [0.006 0.288 0.706], Final Value = $71963.95, Sharpe Ratio = -0.35


Simulation

Simulation Run = 189
Weights = [0.251 0.353 0.395], Final Value = $68679.45, Sharpe Ratio = -0.50


Simulation Run = 190
Weights = [0.279 0.097 0.624], Final Value = $60246.86, Sharpe Ratio = -0.66


Simulation Run = 191
Weights = [0.219 0.582 0.199], Final Value = $76360.02, Sharpe Ratio = -0.35


Simulation Run = 192
Weights = [0.167 0.376 0.457], Final Value = $71188.07, Sharpe Ratio = -0.42


Simulation Run = 193
Weights = [0.111 0.484 0.405], Final Value = $75701.03, Sharpe Ratio = -0.33


Simulation Run = 194
Weights = [0.22  0.25  0.529], Final Value = $66210.73, Sharpe Ratio = -0.53


Simulation Run = 195
Weights = [0.395 0.297 0.308], Final Value = $63867.99, Sharpe Ratio = -0.65


Simulation Run = 196
Weights = [0.074 0.491 0.435], Final Value = $76683.40, Sharpe Ratio = -0.30


Simulation Run = 197
Weights = [0.447 0.207 0.346], Final Value = $59980.06, Sharpe Ratio = -0.74


Simulation Run = 198
Weights = [0.218 0.381 0.401], Final Value = $70253.69, Sharpe Ratio = -0.46




Simulation Run = 272
Weights = [0.563 0.347 0.09 ], Final Value = $61782.33, Sharpe Ratio = -0.75


Simulation Run = 273
Weights = [0.405 0.379 0.216], Final Value = $66155.02, Sharpe Ratio = -0.61


Simulation Run = 274
Weights = [0.204 0.451 0.345], Final Value = $72677.18, Sharpe Ratio = -0.41


Simulation Run = 275
Weights = [0.502 0.136 0.362], Final Value = $56642.12, Sharpe Ratio = -0.83


Simulation Run = 276
Weights = [0.357 0.332 0.311], Final Value = $65774.51, Sharpe Ratio = -0.60


Simulation Run = 277
Weights = [0.168 0.627 0.205], Final Value = $78833.98, Sharpe Ratio = -0.29


Simulation Run = 278
Weights = [0.47  0.219 0.31 ], Final Value = $59872.77, Sharpe Ratio = -0.76


Simulation Run = 279
Weights = [0.542 0.075 0.383], Final Value = $53923.78, Sharpe Ratio = -0.90


Simulation Run = 280
Weights = [0.386 0.223 0.391], Final Value = $61779.50, Sharpe Ratio = -0.68


Simulation Run = 281
Weights = [0.233 0.432 0.335], Final Value = $71488.09, Sharpe Ratio = -0.44




Simulation Run = 356
Weights = [0.405 0.42  0.176], Final Value = $67409.29, Sharpe Ratio = -0.58


Simulation Run = 357
Weights = [0.05  0.114 0.837], Final Value = $65699.97, Sharpe Ratio = -0.46


Simulation Run = 358
Weights = [0.028 0.53  0.442], Final Value = $78891.35, Sharpe Ratio = -0.25


Simulation Run = 359
Weights = [0.339 0.279 0.382], Final Value = $64536.04, Sharpe Ratio = -0.61


Simulation Run = 360
Weights = [0.055 0.469 0.476], Final Value = $76446.30, Sharpe Ratio = -0.30


Simulation Run = 361
Weights = [0.229 0.387 0.384], Final Value = $70199.93, Sharpe Ratio = -0.47


Simulation Run = 362
Weights = [0.82  0.116 0.063], Final Value = $49167.38, Sharpe Ratio = -1.06


Simulation Run = 363
Weights = [0.302 0.54  0.157], Final Value = $73288.69, Sharpe Ratio = -0.43


Simulation Run = 364
Weights = [0.028 0.555 0.417], Final Value = $79673.17, Sharpe Ratio = -0.24


Simulation Run = 365
Weights = [0.65  0.086 0.265], Final Value = $51924.43, Sharpe Ratio = -0.97




...

Simulation Run = 9620
Weights = [0.482 0.12  0.399], Final Value = $56569.18, Sharpe Ratio = -0.82


Simulation Run = 9621
Weights = [0.261 0.337 0.402], Final Value = $67971.90, Sharpe Ratio = -0.52


Simulation Run = 9622
Weights = [0.549 0.424 0.027], Final Value = $64413.18, Sharpe Ratio = -0.69


Simulation Run = 9623
Weights = [0.721 0.239 0.039], Final Value = $55065.41, Sharpe Ratio = -0.93


Simulation Run = 9624
Weights = [0.343 0.588 0.069], Final Value = $73889.39, Sharpe Ratio = -0.43


Simulation Run = 9625
Weights = [0.199 0.262 0.539], Final Value = $66992.79, Sharpe Ratio = -0.51


Simulation Run = 9626
Weights = [0.397 0.457 0.146], Final Value = $68704.06, Sharpe Ratio = -0.55


Simulation Run = 9627
Weights = [0.563 0.426 0.011], Final Value = $64171.58, Sharpe Ratio = -0.70


Simulation Run = 9628
Weights = [0.308 0.331 0.361], Final Value = $66795.98, Sharpe Ratio = -0.56


Simulation Run = 9629
Weights = [0.085 0.508 0.407], Final Value = $76990.47, Sharpe Ratio 

Simulation Run = 9702
Weights = [0.371 0.445 0.184], Final Value = $68888.03, Sharpe Ratio = -0.54


Simulation Run = 9703
Weights = [0.622 0.234 0.143], Final Value = $57049.70, Sharpe Ratio = -0.86


Simulation Run = 9704
Weights = [0.199 0.236 0.565], Final Value = $66225.77, Sharpe Ratio = -0.52


Simulation Run = 9705
Weights = [0.212 0.263 0.525], Final Value = $66774.20, Sharpe Ratio = -0.52


Simulation Run = 9706
Weights = [0.026 0.1   0.874], Final Value = $65810.37, Sharpe Ratio = -0.44


Simulation Run = 9707
Weights = [0.167 0.552 0.282], Final Value = $76565.39, Sharpe Ratio = -0.33


Simulation Run = 9708
Weights = [0.281 0.32  0.398], Final Value = $67032.12, Sharpe Ratio = -0.54


Simulation Run = 9709
Weights = [0.433 0.104 0.464], Final Value = $57149.22, Sharpe Ratio = -0.79


Simulation Run = 9710
Weights = [0.56 0.18 0.26], Final Value = $56746.41, Sharpe Ratio = -0.85


Simulation Run = 9711
Weights = [0.714 0.122 0.164], Final Value = $51627.81, Sharpe Ratio = -

Simulation Run = 9785
Weights = [0.543 0.456 0.001], Final Value = $65509.88, Sharpe Ratio = -0.66


Simulation Run = 9786
Weights = [0.399 0.205 0.396], Final Value = $60965.85, Sharpe Ratio = -0.70


Simulation Run = 9787
Weights = [0.341 0.191 0.468], Final Value = $61795.29, Sharpe Ratio = -0.66


Simulation Run = 9788
Weights = [0.504 0.276 0.219], Final Value = $60879.81, Sharpe Ratio = -0.75


Simulation Run = 9789
Weights = [0.471 0.335 0.194], Final Value = $63387.56, Sharpe Ratio = -0.69


Simulation Run = 9790
Weights = [0.444 0.134 0.422], Final Value = $57823.06, Sharpe Ratio = -0.78


Simulation Run = 9791
Weights = [0.657 0.128 0.215], Final Value = $53045.94, Sharpe Ratio = -0.95


Simulation Run = 9792
Weights = [0.066 0.499 0.435], Final Value = $77134.19, Sharpe Ratio = -0.29


Simulation Run = 9793
Weights = [0.035 0.486 0.479], Final Value = $77400.04, Sharpe Ratio = -0.28


Simulation Run = 9794
Weights = [0.241 0.475 0.284], Final Value = $72630.95, Sharpe Ratio 

Simulation Run = 9867
Weights = [0.091 0.591 0.318], Final Value = $79399.68, Sharpe Ratio = -0.26


Simulation Run = 9868
Weights = [0.194 0.442 0.365], Final Value = $72627.47, Sharpe Ratio = -0.41


Simulation Run = 9869
Weights = [0.354 0.424 0.222], Final Value = $68638.30, Sharpe Ratio = -0.54


Simulation Run = 9870
Weights = [0.442 0.133 0.424], Final Value = $57851.09, Sharpe Ratio = -0.78


Simulation Run = 9871
Weights = [0.072 0.609 0.319], Final Value = $80341.73, Sharpe Ratio = -0.24


Simulation Run = 9872
Weights = [0.206 0.35  0.444], Final Value = $69547.37, Sharpe Ratio = -0.47


Simulation Run = 9873
Weights = [0.145 0.216 0.639], Final Value = $66772.95, Sharpe Ratio = -0.49


Simulation Run = 9874
Weights = [0.452 0.35  0.197], Final Value = $64245.45, Sharpe Ratio = -0.66


Simulation Run = 9875
Weights = [0.096 0.269 0.635], Final Value = $69437.07, Sharpe Ratio = -0.42


Simulation Run = 9876
Weights = [0.354 0.008 0.637], Final Value = $55924.38, Sharpe Ratio 

Simulation Run = 9967
Weights = [0.141 0.2   0.659], Final Value = $66356.63, Sharpe Ratio = -0.49


Simulation Run = 9968
Weights = [0.562 0.248 0.19 ], Final Value = $58770.17, Sharpe Ratio = -0.81


Simulation Run = 9969
Weights = [0.311 0.129 0.56 ], Final Value = $60548.07, Sharpe Ratio = -0.67


Simulation Run = 9970
Weights = [0.423 0.177 0.4  ], Final Value = $59602.49, Sharpe Ratio = -0.74


Simulation Run = 9971
Weights = [0.406 0.264 0.33 ], Final Value = $62641.06, Sharpe Ratio = -0.68


Simulation Run = 9972
Weights = [0.116 0.639 0.245], Final Value = $80320.30, Sharpe Ratio = -0.25


Simulation Run = 9973
Weights = [0.231 0.706 0.063], Final Value = $79898.58, Sharpe Ratio = -0.29


Simulation Run = 9974
Weights = [0.132 0.726 0.142], Final Value = $82646.12, Sharpe Ratio = -0.22


Simulation Run = 9975
Weights = [0.558 0.02  0.422], Final Value = $51908.18, Sharpe Ratio = -0.94


Simulation Run = 9976
Weights = [0.368 0.272 0.36 ], Final Value = $63662.21, Sharpe Ratio 

In [42]:
sharpe_ratio_runs.argmax()

8093

In [43]:
optimal_weights=weights_runs[sharpe_ratio_runs.argmax(), :] # optimal weights
optimal_weights.round(3)

array([0.005, 0.972, 0.022])

In [44]:
optimal_portfolio_return, optimal_volatility, optimal_sharpe_ratio, highest_final_value, optimal_return_on_investment = simulation_engine(weights_runs[sharpe_ratio_runs.argmax(), :], initial_investment)

In [45]:
print('Best Portfolio Metrics Based on {} Monte Carlo Simulation Runs:'.format(sim_runs))
print('  - Portfolio Expected Annual Return = {:.02f}%'.format(optimal_portfolio_return * 100))
print('  - Portfolio Standard Deviation (Volatility) = {:.02f}%'.format(optimal_volatility * 100))
print('  - Sharpe Ratio = {:.02f}'.format(optimal_sharpe_ratio))
print('  - Final Value = VND{:.02f}'.format(highest_final_value))
print('  - Return on Investment = {:.02f}%'.format(optimal_return_on_investment))

Best Portfolio Metrics Based on 10000 Monte Carlo Simulation Runs:
  - Portfolio Expected Annual Return = 3.48%
  - Portfolio Standard Deviation (Volatility) = 34.97%
  - Sharpe Ratio = -0.04
  - Final Value = VND92892.29
  - Return on Investment = -7.11%


In [46]:
sim_out_df = pd.DataFrame({'Volatility': volatility_runs.tolist(), 'Portfolio_Return': expected_portfolio_returns_runs.tolist(), 'Sharpe_Ratio': np.abs(sharpe_ratio_runs).tolist() })
sim_out_df
import plotly.graph_objects as go
import plotly.express as px
fig = px.scatter(sim_out_df, x = 'Volatility', y = 'Portfolio_Return', color = 'Sharpe_Ratio', size = 'Sharpe_Ratio', hover_data = ['Sharpe_Ratio'] )
fig.update_layout({'plot_bgcolor': "white"})
fig.show()

In [47]:
fig = px.scatter(sim_out_df, x = 'Volatility', y = 'Portfolio_Return', color = 'Sharpe_Ratio', size = 'Sharpe_Ratio', hover_data = ['Sharpe_Ratio'] )
fig.add_trace(go.Scatter(x = [optimal_volatility], y = [optimal_portfolio_return], mode = 'markers', name = 'Optimal Point', marker = dict(size=[40], color = 'red')))
fig.update_layout(coloraxis_colorbar = dict(y = 0.7, dtick = 5))
fig.update_layout({'plot_bgcolor': "white"})
fig.show()